In [1]:
import sys, os
sys.path.insert(0, '/home/hossay/gaitanalysis/src/dev')

os.environ["CUDA_DEVICE_ORDER"]="PCI_BUS_ID"   # see issue #152
os.environ["CUDA_VISIBLE_DEVICES"]="3"

import torch
import torch.nn as nn
import numpy as np
from torch.utils.data import DataLoader
import torchvision.transforms as TF
from utils.transforms import (
    Compose, ToTensor, MultiScaleRandomCrop, MultiScaleCornerCrop, Normalize,
    TemporalRandomCrop, TemporalCenterCrop, LoopPadding)
import models
from utils.generate_model import load_pretrained_ckpt, generate_backbone
from utils.mean import get_mean, get_std
import datasets.gaitregression
from collections import namedtuple
from itertools import chain
from sklearn.preprocessing import StandardScaler
from scipy.ndimage import zoom
import cv2
from tqdm import tqdm
import copy

Opt = namedtuple('opts', ['ckpt_dir', 'attention_str', 'model_arch', 'merge_type', 'arch', 'group_str', 
                          'pretrain_epoch', 'test_epoch',
                          'backbone', 'pretrained_path', 'sample_duration', 'sample_size', 'img_size', 
                          'raw_h', 'raw_w',
                          'load_pretrained',
                          'norm_value', 'mean_dataset', 'data_root'])

opt = Opt(ckpt_dir='../ckpt_repos', attention_str='NonAttentive',
          model_arch='Guideless',
          merge_type='',
          arch='r2plus1d_18-18',
          group_str='', 
          pretrain_epoch='160', test_epoch=40,
          backbone='r2plus1d_18',
          pretrained_path='',
          sample_duration=64,
          sample_size=112,
          img_size=144,
          raw_h=480, raw_w=640,
          load_pretrained=False,
          norm_value=255,
          mean_dataset='kinetics',
          data_root="/data/GaitData/RawFrames"
         )



# dataset statics
mean = get_mean(opt.norm_value, dataset=opt.mean_dataset)
std = get_std(opt.norm_value, dataset=opt.mean_dataset)

# target columns to eval
target_columns = ['Velocity', 'Cadence', 'Cycle Time(sec)/L', 'Cycle Time(sec)/R',
         'Stride Length(cm)/L', 'Stride Length(cm)/R', 'HH Base Support(cm)/L',
         'HH Base Support(cm)/R', 'Swing % of Cycle/L', 'Swing % of Cycle/R',
         'Stance % of Cycle/L', 'Stance % of Cycle/R', 'Double Supp % Cycle/L',
         'Double Supp % Cycle/R', 'Toe In / Out/L', 'Toe In / Out/R']


def get_mlist():
    
    """
        moduel List to register to forward hook  ####
    """
    
    bm_seq = lambda prime, i : [f'{prime}.{branch}_layers.{i}' for branch in ['backbone', 'matching' ]] 

    m_list = [ *list(chain(*[ bm_seq('agnet', i) for i in range(4)])),
              'agnet.conv_1x1',
              'agnet.fc' ]
    return m_list

def get_activation(m_dict, activation_layer, activation='relu'):
    A_k = m_dict[activation_layer]
    
    # move CUDA tensor to CPU
    A_k = A_k.cpu()
            
    # remove batch dim
    conv_out = A_k.data[0].numpy()
    
    # average
    conv_out = np.mean(conv_out, axis=0)
            
    # upsample grad_cam
    temporal_ratio = 64 / conv_out.shape[0]
    spatial_ratio = 112 / conv_out.shape[1]
    
    conv_out = zoom(conv_out, (temporal_ratio, spatial_ratio, spatial_ratio))
    
    
    if activation=='relu':
        conv_out = np.maximum(conv_out, 0)
    elif activation=='sigmoid':
        conv_out = 1/(1 + np.exp(-x))

    conv_out = conv_out / conv_out.max((1,2))[:,None,None]
    
    return conv_out


def generate_grad_cam(m_dict, p_index, activation_layer):
    y_c = torch.cat((m_dict['pretrained_agnet.fc'], m_dict['agnet.fc']), 1)[0, p_index]
    A_k = m_dict[activation_layer]
            
    grad_val = torch.autograd.grad(y_c, A_k, retain_graph=True)[0].data
    
    # move CUDA tensor to CPU
    A_k = A_k.cpu()
    grad_val = grad_val.cpu()

    # remove batch dim
    conv_out = A_k.data[0].numpy()
    grad_val = grad_val[0].numpy()
    
    weights = np.mean(grad_val, axis=(1,2,3))
    #grad_cam = weights * conv_out
    
    grad_cam = np.zeros(dtype=np.float32, shape=conv_out.shape[1:])
    for k, w in enumerate(weights):
        grad_cam += w * conv_out[k]
        
    # upsample grad_cam
    temporal_ratio = 64 / grad_cam.shape[0]
    spatial_ratio = 112 / grad_cam.shape[1]
    
    grad_cam = zoom(grad_cam, (temporal_ratio, spatial_ratio, spatial_ratio))
    
    positive_grad_cam = np.maximum(grad_cam, 0)
    negative_grad_cam = np.maximum(-grad_cam, 0)
        
    positive_grad_cam = positive_grad_cam / positive_grad_cam.max((1,2))[:,None,None]
    negative_grad_cam = negative_grad_cam / negative_grad_cam.max((1,2))[:,None,None]
        
    return positive_grad_cam, negative_grad_cam

In [2]:
backbone = generate_backbone(opt)
net = models.regression_model.GuidelessNet(backbone, hidden_size=512, out_size=16, drop_rate=0.0, freeze=False)

if torch.cuda.is_available():
    net.cuda()
net

GuidelessNet(
  (stem): R2Plus1dStem(
    (0): Conv3d(3, 45, kernel_size=(1, 7, 7), stride=(1, 2, 2), padding=(0, 3, 3), bias=False)
    (1): BatchNorm3d(45, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    (2): ReLU(inplace=True)
    (3): Conv3d(45, 64, kernel_size=(3, 1, 1), stride=(1, 1, 1), padding=(1, 0, 0), bias=False)
    (4): BatchNorm3d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    (5): ReLU(inplace=True)
  )
  (backbone): Sequential(
    (0): Sequential(
      (0): BasicBlock(
        (conv1): Sequential(
          (0): Conv2Plus1D(
            (0): Conv3d(64, 144, kernel_size=(1, 3, 3), stride=(1, 1, 1), padding=(0, 1, 1), bias=False)
            (1): BatchNorm3d(144, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
            (2): ReLU(inplace=True)
            (3): Conv3d(144, 64, kernel_size=(3, 1, 1), stride=(1, 1, 1), padding=(1, 0, 0), bias=False)
          )
          (1): BatchNorm3d(64, eps=1e-05, momentum

In [3]:
backbone = generate_backbone(opt)
net = models.regression_model.GuidelessNet(backbone, hidden_size=512, out_size=16, drop_rate=0.0, freeze=False)

if torch.cuda.is_available():
    net.cuda()

# global vars
m_list = get_mlist()
m_dict = {}

def hook(m, inp, out):
    global m_list
    global m_dict
        
    layer_name = m_list.pop(0)
    m_dict[layer_name] = out

# register hook for activation visualization
# register hook for activation visualization
net.fc.register_forward_hook(hook)
net.conv_1x1.register_forward_hook(hook)
for i in range(4):
    net.backbone[i].register_forward_hook(hook)
    net.matching_layers[i].register_forward_hook(hook)

In [4]:
def probe_forward_vals(net, img_tensor, m_dict, m_list):
    img_tensor = img_tensor[None, :]    
    
    with torch.no_grad():
        net.eval()
        out = net(img_tensor)
    
    m_list = get_mlist()
    
    return m_dict, m_list

In [5]:
spatial_transform = Compose(
            [
                TF.CenterCrop(opt.sample_size),
                ToTensor(opt.norm_value),
                Normalize(mean, std),
            ]
)

target_transform = StandardScaler()


# prepare dataset  (train/test split)
data = datasets.gaitregression.prepare_dataset(
    input_file="../../../preprocess/data/person_detection_and_tracking_results_drop.pkl",
    target_file="../../../preprocess/data/targets_dataframe.pkl",
    target_columns=target_columns,
    chunk_parts=8,
    target_transform=target_transform,
)

# test dataset
ds = datasets.gaitregression.GAITSegRegDataset(
            X=data["test_X"], y=data["test_y"], opt=opt, phase='test',
            spatial_transform=spatial_transform
        )

In [6]:
def denormalization(img, mean, std):
    return img.permute(1,2,0).numpy()*std + mean

def write_activation_video(net, ds, save_dir,
                           activation_layer='pretrained_agnet.conv_1x1'):
        
    os.system('mkdir -p {}'.format(save_dir))
    
    for i in tqdm(range(len(ds))):
        global m_dict
        global m_list
        
        img_tensor, mask_tensor, target, vid, _ = ds[i]

        if torch.cuda.is_available():
            img_tensor = img_tensor.cuda()

        m_dict, m_list = probe_forward_vals(net, img_tensor, m_dict, m_list)

        # get activation results
        activation_result = get_activation(m_dict, 
                                           activation_layer=activation_layer,
                                           activation='relu')

        out = cv2.VideoWriter(os.path.join(save_dir, vid+'.avi'),
                              cv2.VideoWriter_fourcc('M','J','P','G'), 
                              24.0, (112,112))

        # Move CUDA tensor to CPU
        img_tensor = img_tensor.cpu()

        for t in range(img_tensor.size(1)):
            img_ = np.uint8(255*denormalization(img_tensor[:,t], mean, std))
            heatmap_ = np.uint8(255*activation_result[t])
            heatmap_ = cv2.applyColorMap(heatmap_, cv2.COLORMAP_JET)
            frame = np.uint8(heatmap_*0.3 + img_*0.5)
            out.write(frame)

        out.release()
        

write_activation_video(net, ds, save_dir='/data/GaitData/ActivationMap_videos/GuidelessNet',
                       activation_layer='agnet.conv_1x1')

100%|██████████| 731/731 [11:34<00:00,  1.03it/s]


In [7]:
# T = 20

# p_index = 9
# print(target_columns[p_index])

# positive_grad_cam, negative_grad_cam = generate_grad_cam(m_dict, p_index=p_index, activation_layer='pretrained_agnet.conv_1x1')

# import matplotlib.pyplot as plt

# def denormalization(img, mean, std):
#     return img.permute(1,2,0).numpy()*std + mean

# fig, (ax1, ax2, ax3) = plt.subplots(1,3,figsize=(15,15))

# ax1.imshow(denormalization(img_tensor[:,T], mean, std))
# ax1.set_title('INPUT IMG')

# ax2.imshow(positive_grad_cam[T])
# ax2.set_title('Positive grad-CAM')

# ax3.imshow(negative_grad_cam[T])
# ax3.set_title('Negative grad-CAM')
# plt.show()

In [8]:
# convert *.avi -> *.mp4
!sh convert_video-GuidelessNet.sh

ffmpeg version 2.8.15-0ubuntu0.16.04.1 Copyright (c) 2000-2018 the FFmpeg developers
  built with gcc 5.4.0 (Ubuntu 5.4.0-6ubuntu1~16.04.10) 20160609
  configuration: --prefix=/usr --extra-version=0ubuntu0.16.04.1 --build-suffix=-ffmpeg --toolchain=hardened --libdir=/usr/lib/x86_64-linux-gnu --incdir=/usr/include/x86_64-linux-gnu --cc=cc --cxx=g++ --enable-gpl --enable-shared --disable-stripping --disable-decoder=libopenjpeg --disable-decoder=libschroedinger --enable-avresample --enable-avisynth --enable-gnutls --enable-ladspa --enable-libass --enable-libbluray --enable-libbs2b --enable-libcaca --enable-libcdio --enable-libflite --enable-libfontconfig --enable-libfreetype --enable-libfribidi --enable-libgme --enable-libgsm --enable-libmodplug --enable-libmp3lame --enable-libopenjpeg --enable-libopus --enable-libpulse --enable-librtmp --enable-libschroedinger --enable-libshine --enable-libsnappy --enable-libsoxr --enable-libspeex --enable-libssh --enable-libtheora --enable-libtwolame --

frame=   64 fps=0.0 q=-1.0 Lsize=      18kB time=00:00:02.58 bitrate=  57.3kbits/s    
video:17kB audio:0kB subtitle:0kB other streams:0kB global headers:0kB muxing overhead: 8.546308%
[libx264 @ 0x10fcfe0] frame I:1     Avg QP:26.12  size:  1071
[libx264 @ 0x10fcfe0] frame P:40    Avg QP:25.24  size:   352
[libx264 @ 0x10fcfe0] frame B:23    Avg QP:29.68  size:    54
[libx264 @ 0x10fcfe0] consecutive B-frames: 42.2% 25.0% 14.1% 18.8%
[libx264 @ 0x10fcfe0] mb I  I16..4:  2.0% 87.8% 10.2%
[libx264 @ 0x10fcfe0] mb P  I16..4:  1.0%  3.3%  0.2%  P16..4: 51.9% 24.0%  9.9%  0.0%  0.0%    skip: 9.7%
[libx264 @ 0x10fcfe0] mb B  I16..4:  0.0%  0.0%  0.0%  B16..8: 21.5%  3.5%  1.2%  direct: 2.1%  skip:71.6%  L0:26.0% L1:58.2% BI:15.8%
[libx264 @ 0x10fcfe0] 8x8 transform intra:79.3% inter:70.0%
[libx264 @ 0x10fcfe0] coded y,uvDC,uvAC intra: 70.0% 99.3% 67.4% inter: 22.6% 47.4% 3.7%
[libx264 @ 0x10fcfe0] i16 v,h,dc,p: 65% 20%  0% 15%
[libx264 @ 0x10fcfe0] i8 v,h,dc,ddl,ddr,vr,hd,vl,hu: 26% 18% 28%

frame=   64 fps=0.0 q=-1.0 Lsize=      20kB time=00:00:02.58 bitrate=  63.4kbits/s    
video:19kB audio:0kB subtitle:0kB other streams:0kB global headers:0kB muxing overhead: 8.115666%
[libx264 @ 0x933e20] frame I:1     Avg QP:26.59  size:  1207
[libx264 @ 0x933e20] frame P:34    Avg QP:25.33  size:   431
[libx264 @ 0x933e20] frame B:29    Avg QP:29.47  size:    83
[libx264 @ 0x933e20] consecutive B-frames: 23.4% 37.5% 32.8%  6.2%
[libx264 @ 0x933e20] mb I  I16..4:  8.2% 71.4% 20.4%
[libx264 @ 0x933e20] mb P  I16..4:  1.1%  5.0%  0.4%  P16..4: 49.7% 27.0% 12.1%  0.0%  0.0%    skip: 4.7%
[libx264 @ 0x933e20] mb B  I16..4:  0.1%  0.1%  0.0%  B16..8: 21.2%  5.9%  2.6%  direct: 4.2%  skip:65.9%  L0:31.4% L1:52.8% BI:15.8%
[libx264 @ 0x933e20] 8x8 transform intra:73.9% inter:64.3%
[libx264 @ 0x933e20] coded y,uvDC,uvAC intra: 71.6% 96.9% 58.4% inter: 25.1% 44.7% 3.5%
[libx264 @ 0x933e20] i16 v,h,dc,p: 24% 20% 16% 40%
[libx264 @ 0x933e20] i8 v,h,dc,ddl,ddr,vr,hd,vl,hu: 25% 17% 34%  1%  3%  5

frame=   64 fps=0.0 q=-1.0 Lsize=      22kB time=00:00:02.58 bitrate=  69.2kbits/s    
video:20kB audio:0kB subtitle:0kB other streams:0kB global headers:0kB muxing overhead: 7.058711%
[libx264 @ 0x152fe00] frame I:1     Avg QP:23.61  size:  1290
[libx264 @ 0x152fe00] frame P:41    Avg QP:25.49  size:   397
[libx264 @ 0x152fe00] frame B:22    Avg QP:29.44  size:   119
[libx264 @ 0x152fe00] consecutive B-frames: 39.1% 43.8%  4.7% 12.5%
[libx264 @ 0x152fe00] mb I  I16..4: 10.2% 87.8%  2.0%
[libx264 @ 0x152fe00] mb P  I16..4:  1.0%  6.0%  0.7%  P16..4: 44.9% 27.3% 12.1%  0.0%  0.0%    skip: 7.8%
[libx264 @ 0x152fe00] mb B  I16..4:  0.2%  0.2%  0.1%  B16..8: 20.6%  7.7%  2.6%  direct: 3.6%  skip:65.0%  L0:21.1% L1:56.8% BI:22.1%
[libx264 @ 0x152fe00] 8x8 transform intra:79.0% inter:66.0%
[libx264 @ 0x152fe00] coded y,uvDC,uvAC intra: 70.5% 99.0% 71.0% inter: 25.9% 51.0% 4.4%
[libx264 @ 0x152fe00] i16 v,h,dc,p: 56% 11%  4% 30%
[libx264 @ 0x152fe00] i8 v,h,dc,ddl,ddr,vr,hd,vl,hu: 22% 15% 28%

frame=   64 fps=0.0 q=-1.0 Lsize=      20kB time=00:00:02.58 bitrate=  64.3kbits/s    
video:19kB audio:0kB subtitle:0kB other streams:0kB global headers:0kB muxing overhead: 8.040776%
[libx264 @ 0x189be00] frame I:1     Avg QP:24.61  size:  1142
[libx264 @ 0x189be00] frame P:32    Avg QP:25.68  size:   453
[libx264 @ 0x189be00] frame B:31    Avg QP:29.52  size:    93
[libx264 @ 0x189be00] consecutive B-frames: 17.2% 43.8% 32.8%  6.2%
[libx264 @ 0x189be00] mb I  I16..4:  6.1% 93.9%  0.0%
[libx264 @ 0x189be00] mb P  I16..4:  0.8%  4.6%  0.4%  P16..4: 46.6% 31.6% 11.5%  0.0%  0.0%    skip: 4.3%
[libx264 @ 0x189be00] mb B  I16..4:  0.0%  0.0%  0.0%  B16..8: 17.3%  6.1%  1.8%  direct: 3.1%  skip:71.7%  L0:24.6% L1:54.9% BI:20.5%
[libx264 @ 0x189be00] 8x8 transform intra:83.7% inter:65.6%
[libx264 @ 0x189be00] coded y,uvDC,uvAC intra: 77.7% 96.5% 78.7% inter: 22.8% 43.1% 4.6%
[libx264 @ 0x189be00] i16 v,h,dc,p: 25%  0%  0% 75%
[libx264 @ 0x189be00] i8 v,h,dc,ddl,ddr,vr,hd,vl,hu: 36% 10% 17%

...

frame=   64 fps=0.0 q=-1.0 Lsize=      17kB time=00:00:02.58 bitrate=  52.6kbits/s    
video:15kB audio:0kB subtitle:0kB other streams:0kB global headers:0kB muxing overhead: 10.013602%
[libx264 @ 0x1964fe0] frame I:1     Avg QP:21.80  size:  1157
[libx264 @ 0x1964fe0] frame P:31    Avg QP:24.85  size:   380
[libx264 @ 0x1964fe0] frame B:32    Avg QP:27.97  size:    57
[libx264 @ 0x1964fe0] consecutive B-frames: 21.9% 31.2%  9.4% 37.5%
[libx264 @ 0x1964fe0] mb I  I16..4:  2.0% 95.9%  2.0%
[libx264 @ 0x1964fe0] mb P  I16..4:  0.9%  7.0%  0.7%  P16..4: 50.7% 25.9%  8.7%  0.0%  0.0%    skip: 6.3%
[libx264 @ 0x1964fe0] mb B  I16..4:  0.0%  0.1%  0.0%  B16..8: 19.3%  2.6%  0.4%  direct: 1.8%  skip:75.9%  L0:35.8% L1:51.9% BI:12.2%
[libx264 @ 0x1964fe0] 8x8 transform intra:86.0% inter:77.3%
[libx264 @ 0x1964fe0] coded y,uvDC,uvAC intra: 77.8% 95.0% 76.0% inter: 18.6% 41.1% 4.8%
[libx264 @ 0x1964fe0] i16 v,h,dc,p: 29% 21%  7% 43%
[libx264 @ 0x1964fe0] i8 v,h,dc,ddl,ddr,vr,hd,vl,hu: 28% 19% 23

[libx264 @ 0x2228260] using cpu capabilities: MMX2 SSE2Fast SSSE3 SSE4.2 AVX FMA3 AVX2 LZCNT BMI2
[libx264 @ 0x2228260] profile High, level 1.0
[libx264 @ 0x2228260] 264 - core 148 r2643 5c65704 - H.264/MPEG-4 AVC codec - Copyleft 2003-2015 - http://www.videolan.org/x264.html - options: cabac=1 ref=3 deblock=1:0:0 analyse=0x3:0x113 me=hex subme=7 psy=1 psy_rd=1.00:0.00 mixed_ref=1 me_range=16 chroma_me=1 trellis=1 8x8dct=1 cqm=0 deadzone=21,11 fast_pskip=1 chroma_qp_offset=-2 threads=3 lookahead_threads=1 sliced_threads=0 nr=0 decimate=1 interlaced=0 bluray_compat=0 constrained_intra=0 bframes=3 b_pyramid=2 b_adapt=1 b_bias=0 direct=1 weightb=1 open_gop=0 weightp=2 keyint=250 keyint_min=24 scenecut=40 intra_refresh=0 rc_lookahead=40 rc=crf mbtree=1 crf=23.0 qcomp=0.60 qpmin=0 qpmax=69 qpstep=4 ip_ratio=1.40 aq=1:1.00
Output #0, mp4, to '/data/GaitData/ActivationMap_videos/GuidelessNet/mp4/966358_test_0_trial_0.mp4':
  Metadata:
    encoder         : Lavf56.40.101
    Stream #0:0: Video

[libx264 @ 0x1946080] profile High, level 1.0
[libx264 @ 0x1946080] 264 - core 148 r2643 5c65704 - H.264/MPEG-4 AVC codec - Copyleft 2003-2015 - http://www.videolan.org/x264.html - options: cabac=1 ref=3 deblock=1:0:0 analyse=0x3:0x113 me=hex subme=7 psy=1 psy_rd=1.00:0.00 mixed_ref=1 me_range=16 chroma_me=1 trellis=1 8x8dct=1 cqm=0 deadzone=21,11 fast_pskip=1 chroma_qp_offset=-2 threads=3 lookahead_threads=1 sliced_threads=0 nr=0 decimate=1 interlaced=0 bluray_compat=0 constrained_intra=0 bframes=3 b_pyramid=2 b_adapt=1 b_bias=0 direct=1 weightb=1 open_gop=0 weightp=2 keyint=250 keyint_min=24 scenecut=40 intra_refresh=0 rc_lookahead=40 rc=crf mbtree=1 crf=23.0 qcomp=0.60 qpmin=0 qpmax=69 qpstep=4 ip_ratio=1.40 aq=1:1.00
Output #0, mp4, to '/data/GaitData/ActivationMap_videos/GuidelessNet/mp4/982993_test_0_trial_0.mp4':
  Metadata:
    encoder         : Lavf56.40.101
    Stream #0:0: Video: h264 (libx264) ([33][0][0][0] / 0x0021), yuvj420p(pc), 112x112, q=-1--1, 24 fps, 12288 tbn, 24 t

No pixel format specified, yuvj420p for H.264 encoding chosen.
Use -pix_fmt yuv420p for compatibility with outdated media players.
[libx264 @ 0xfbd080] using cpu capabilities: MMX2 SSE2Fast SSSE3 SSE4.2 AVX FMA3 AVX2 LZCNT BMI2
[libx264 @ 0xfbd080] profile High, level 1.0
[libx264 @ 0xfbd080] 264 - core 148 r2643 5c65704 - H.264/MPEG-4 AVC codec - Copyleft 2003-2015 - http://www.videolan.org/x264.html - options: cabac=1 ref=3 deblock=1:0:0 analyse=0x3:0x113 me=hex subme=7 psy=1 psy_rd=1.00:0.00 mixed_ref=1 me_range=16 chroma_me=1 trellis=1 8x8dct=1 cqm=0 deadzone=21,11 fast_pskip=1 chroma_qp_offset=-2 threads=3 lookahead_threads=1 sliced_threads=0 nr=0 decimate=1 interlaced=0 bluray_compat=0 constrained_intra=0 bframes=3 b_pyramid=2 b_adapt=1 b_bias=0 direct=1 weightb=1 open_gop=0 weightp=2 keyint=250 keyint_min=24 scenecut=40 intra_refresh=0 rc_lookahead=40 rc=crf mbtree=1 crf=23.0 qcomp=0.60 qpmin=0 qpmax=69 qpstep=4 ip_ratio=1.40 aq=1:1.00
Output #0, mp4, to '/data/GaitData/Activati

[mjpeg @ 0xb53060] Changeing bps to 8
Input #0, avi, from '/data/GaitData/ActivationMap_videos/GuidelessNet/am022_test_1_trial_1.avi':
  Metadata:
    encoder         : Lavf58.26.101
  Duration: 00:00:02.67, start: 0.000000, bitrate: 407 kb/s
    Stream #0:0: Video: mjpeg (MJPG / 0x47504A4D), yuvj420p(pc, bt470bg/unknown/unknown), 112x112, 391 kb/s, 24 fps, 24 tbr, 24 tbn, 24 tbc
No pixel format specified, yuvj420p for H.264 encoding chosen.
Use -pix_fmt yuv420p for compatibility with outdated media players.
[libx264 @ 0xb58e20] using cpu capabilities: MMX2 SSE2Fast SSSE3 SSE4.2 AVX FMA3 AVX2 LZCNT BMI2
[libx264 @ 0xb58e20] profile High, level 1.0
[libx264 @ 0xb58e20] 264 - core 148 r2643 5c65704 - H.264/MPEG-4 AVC codec - Copyleft 2003-2015 - http://www.videolan.org/x264.html - options: cabac=1 ref=3 deblock=1:0:0 analyse=0x3:0x113 me=hex subme=7 psy=1 psy_rd=1.00:0.00 mixed_ref=1 me_range=16 chroma_me=1 trellis=1 8x8dct=1 cqm=0 deadzone=21,11 fast_pskip=1 chroma_qp_offset=-2 threads=

In [10]:
from IPython.display import HTML
HTML("""
<video src="videos/GuidelessNet/mp4/7160698_test_0_trial_0.mp4" width="448" height="448" controls>
</video>
""")